## Preparação de dados

### Imports

In [1]:
#!pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip

In [2]:
import random
import numpy as np
import pandas as pd
from pandas_profiling import ProfileReport

import seaborn as sns
import matplotlib
import matplotlib.pyplot as plt

%matplotlib inline

In [3]:
print(f'Versão Pandas: {pd.__version__}')
print(f'Versão Numpy: {np.__version__}')
print(f'Versão Seaborn: {sns.__version__}')
print(f'Versão Matplotlib: {matplotlib.__version__}')

Versão Pandas: 1.0.3
Versão Numpy: 1.18.2
Versão Seaborn: 0.10.1
Versão Matplotlib: 3.2.1


### Loading data

In [4]:
!curl --remote-name \
     -H 'Accept: application/vnd.github.v3.raw' \
     --location https://raw.githubusercontent.com/datasciencedojo/datasets/master/titanic.csv

titanic_orig = pd.read_csv('titanic.csv')
titanic_orig.drop(columns=['PassengerId'], inplace=True)
titanic_orig.head()

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 60302  100 60302    0     0   205k      0 --:--:-- --:--:-- --:--:--  205k


Survived  Pclass                                               Name  \
0         0       3                            Braund, Mr. Owen Harris   
1         1       1  Cumings, Mrs. John Bradley (Florence Briggs Th...   
2         1       3                             Heikkinen, Miss. Laina   
3         1       1       Futrelle, Mrs. Jacques Heath (Lily May Peel)   
4         0       3                           Allen, Mr. William Henry   

      Sex   Age  SibSp  Parch            Ticket     Fare Cabin Embarked  
0    male  22.0      1      0         A/5 21171   7.2500   NaN        S  
1  female  38.0      1      0          PC 17599  71.2833   C85        C  
2  female  26.0      0      0  STON/O2. 3101282   7.9250   NaN        S  
3  female  35.0      1      0            113803  53.1000  C123        S  
4    male  35.0      0      0            373450   8.0500   NaN        S

### Dicionário de Dados

<b>Sobreviveu?:</b> Informa se o passageiro sobreviveu ao desastre. 0 = Não; 1 = Sim<br>
<b>Classe:</b> Classe na qual o passageiro viajou. 1 = Primeira Classe; 2 = Segunda Classe; 3 = Terceira Classe<br>
<b>Nome:</b> Nome do passageiro<br>
<b>Sexo:</b> Sexo do passageiro<br>
<b>Idade:</b> Idade do passageiro<br>
<b>SibSp:</b> Informa a quantidade de irmãos e cônjuges que o paciente possuía na embarcação<br>
<b>Parch:</b> Quantidade de crianças e idosos (pais) relativos ao passageiro<br>
<b>Ticket:</b> Identificador da passagem<br>
<b>Fare:</b> Valor da passagem<br>
<b>Cabin:</b> Número da cabine do passageiro<br>
<b>Embarked:</b> Local onde o passageiro embarcou<br>

### Data profiling

In [5]:
report = titanic_orig.profile_report(sort='None', html={'style':{'full_width':True}}, progress_bar=False)
report.to_notebook_iframe()

### Dropping missing values

In [6]:
titanic = titanic_orig.copy()

titanic.dropna(how='all', inplace=True)
titanic.dropna(how='all', subset=['Name', 'Age'], inplace=True)
titanic.dropna(how='any', subset=['Name', 'Age'], inplace=True)
titanic.dropna(inplace=True)

report = titanic.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report.to_notebook_iframe()

### Filling missing values with mean, meadian, mode

In [7]:
titanic = titanic_orig.copy()

titanic.fillna(titanic.median(), inplace=True)
titanic['Embarked'].fillna(titanic['Embarked'].mode()[0], inplace=True)
titanic['Cabin'].fillna(titanic['Cabin'].mode()[0], inplace=True)

report = titanic.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report.to_notebook_iframe()

### Filling missing values with prediction / Infering missing values

#### Predição Idade

In [8]:
from sklearn import tree
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVR

In [9]:
titanic = titanic_orig.copy()
titanic.drop(['Name','Ticket','Cabin', 'Sex', 'Embarked'], axis=1, inplace = True)

test = titanic[titanic['Age'].isnull()]
titanic.dropna(inplace=True)

X = titanic.drop(['Age'], 1)
y = titanic['Age']

In [10]:
parameters = parameters = {
    'kernel': ['rbf', 'sigmoid'], 
    'C': np.logspace(np.log10(0.001), np.log10(200), num=20), 
    'gamma': np.logspace(np.log10(0.0001), np.log10(2), num=20)
}

model = GridSearchCV(SVR(), param_grid=parameters, cv=5, verbose=5)
model.fit(X, y)

test.drop(['Age'], 1, inplace=True)
new_age = model.predict(test)
test['new_age'] = new_age

Fitting 5 folds for each of 800 candidates, totalling 4000 fits
[CV] C=0.001, gamma=0.0001, kernel=rbf ...............................
[CV] .. C=0.001, gamma=0.0001, kernel=rbf, score=-0.003, total=   0.0s
[CV] C=0.001, gamma=0.0001, kernel=rbf ...............................
[CV] .. C=0.001, gamma=0.0001, kernel=rbf, score=-0.015, total=   0.0s
[CV] C=0.001, gamma=0.0001, kernel=rbf ...............................
[CV] .. C=0.001, gamma=0.0001, kernel=rbf, score=-0.016, total=   0.0s
[CV] C=0.001, gamma=0.0001, kernel=rbf ...............................
[CV] .. C=0.001, gamma=0.0001, kernel=rbf, score=-0.098, total=   0.0s
[CV] C=0.001, gamma=0.0001, kernel=rbf ...............................
[CV] ... C=0.001, gamma=0.0001, kernel=rbf, score=0.000, total=   0.0s
[CV] C=0.001, gamma=0.0001, kernel=sigmoid ...........................
[CV]  C=0.001, gamma=0.0001, kernel=sigmoid, score=-0.003, total=   0.0s
[CV] C=0.001, gamma=0.0001, kernel=sigmoid ...........................
[CV]  C=0.0

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.1s remaining:    0.0s


[CV]  C=0.001, gamma=0.0001, kernel=sigmoid, score=0.000, total=   0.0s
[CV] C=0.001, gamma=0.00016841082361039716, kernel=rbf ...............
[CV]  C=0.001, gamma=0.00016841082361039716, kernel=rbf, score=-0.003, total=   0.0s
[CV] C=0.001, gamma=0.00016841082361039716, kernel=rbf ...............
[CV]  C=0.001, gamma=0.00016841082361039716, kernel=rbf, score=-0.015, total=   0.0s
[CV] C=0.001, gamma=0.00016841082361039716, kernel=rbf ...............
[CV]  C=0.001, gamma=0.00016841082361039716, kernel=rbf, score=-0.016, total=   0.0s
[CV] C=0.001, gamma=0.00016841082361039716, kernel=rbf ...............
[CV]  C=0.001, gamma=0.00016841082361039716, kernel=rbf, score=-0.098, total=   0.0s
[CV] C=0.001, gamma=0.00016841082361039716, kernel=rbf ...............
[CV]  C=0.001, gamma=0.00016841082361039716, kernel=rbf, score=0.000, total=   0.0s
[CV] C=0.001, gamma=0.00016841082361039716, kernel=sigmoid ...........
[CV]  C=0.001, gamma=0.00016841082361039716, kernel=sigmoid, score=-0.003, tot

[CV]  C=0.001, gamma=0.0022814975074036316, kernel=sigmoid, score=-0.000, total=   0.0s
[CV] C=0.001, gamma=0.003842288742869134, kernel=rbf .................
[CV]  C=0.001, gamma=0.003842288742869134, kernel=rbf, score=-0.003, total=   0.0s
[CV] C=0.001, gamma=0.003842288742869134, kernel=rbf .................
[CV]  C=0.001, gamma=0.003842288742869134, kernel=rbf, score=-0.016, total=   0.0s
[CV] C=0.001, gamma=0.003842288742869134, kernel=rbf .................
[CV]  C=0.001, gamma=0.003842288742869134, kernel=rbf, score=-0.015, total=   0.0s
[CV] C=0.001, gamma=0.003842288742869134, kernel=rbf .................
[CV]  C=0.001, gamma=0.003842288742869134, kernel=rbf, score=-0.098, total=   0.0s
[CV] C=0.001, gamma=0.003842288742869134, kernel=rbf .................
[CV]  C=0.001, gamma=0.003842288742869134, kernel=rbf, score=0.000, total=   0.0s
[CV] C=0.001, gamma=0.003842288742869134, kernel=sigmoid .............
[CV]  C=0.001, gamma=0.003842288742869134, kernel=sigmoid, score=-0.003,

[CV]  C=0.001, gamma=0.05205230876288979, kernel=sigmoid, score=-0.000, total=   0.0s
[CV] C=0.001, gamma=0.08766172189580963, kernel=rbf ..................
[CV]  C=0.001, gamma=0.08766172189580963, kernel=rbf, score=-0.003, total=   0.0s
[CV] C=0.001, gamma=0.08766172189580963, kernel=rbf ..................
[CV]  C=0.001, gamma=0.08766172189580963, kernel=rbf, score=-0.015, total=   0.0s
[CV] C=0.001, gamma=0.08766172189580963, kernel=rbf ..................
[CV]  C=0.001, gamma=0.08766172189580963, kernel=rbf, score=-0.016, total=   0.0s
[CV] C=0.001, gamma=0.08766172189580963, kernel=rbf ..................
[CV]  C=0.001, gamma=0.08766172189580963, kernel=rbf, score=-0.097, total=   0.0s
[CV] C=0.001, gamma=0.08766172189580963, kernel=rbf ..................
[CV]  C=0.001, gamma=0.08766172189580963, kernel=rbf, score=0.000, total=   0.0s
[CV] C=0.001, gamma=0.08766172189580963, kernel=sigmoid ..............
[CV]  C=0.001, gamma=0.08766172189580963, kernel=sigmoid, score=-0.003, total= 

...

[CV]  C=200.00000000000003, gamma=0.0001, kernel=sigmoid, score=-30369.141, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0001, kernel=sigmoid ..............
[CV]  C=200.00000000000003, gamma=0.0001, kernel=sigmoid, score=-12530.938, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0001, kernel=sigmoid ..............
[CV]  C=200.00000000000003, gamma=0.0001, kernel=sigmoid, score=-18673.670, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0001, kernel=sigmoid ..............
[CV]  C=200.00000000000003, gamma=0.0001, kernel=sigmoid, score=-21059.121, total=   0.0s
[CV] C=200.00000000000003, gamma=0.00016841082361039716, kernel=rbf ..
[CV]  C=200.00000000000003, gamma=0.00016841082361039716, kernel=rbf, score=0.272, total=   0.0s
[CV] C=200.00000000000003, gamma=0.00016841082361039716, kernel=rbf ..
[CV]  C=200.00000000000003, gamma=0.00016841082361039716, kernel=rbf, score=0.125, total=   0.0s
[CV] C=200.00000000000003, gamma=0.00016841082361039716, kernel=rbf ..
[CV]  C=200.00000000

[CV]  C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf, score=0.298, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf ...
[CV]  C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf, score=0.152, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf ...
[CV]  C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf, score=0.149, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf ...
[CV]  C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf, score=0.139, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf ...
[CV]  C=200.00000000000003, gamma=0.0022814975074036316, kernel=rbf, score=0.116, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0022814975074036316, kernel=sigmoid 
[CV]  C=200.00000000000003, gamma=0.0022814975074036316, kernel=sigmoid, score=-351324.790, total=   0.0s
[CV] C=200.00000000000003, gamma=0.0022814975074036316, ke

[CV]  C=200.00000000000003, gamma=0.030907935515657823, kernel=rbf, score=-0.049, total=   0.0s
[CV] C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid 
[CV]  C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid, score=-1574.894, total=   0.0s
[CV] C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid 
[CV]  C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid, score=-4659.154, total=   0.0s
[CV] C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid 
[CV]  C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid, score=-2913.835, total=   0.0s
[CV] C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid 
[CV]  C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid, score=-2140.901, total=   0.0s
[CV] C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid 
[CV]  C=200.00000000000003, gamma=0.030907935515657823, kernel=sigmoid, score=-3008.968, total=   0.0s
[CV] C=200.00000000000003, gamma=0

[CV]  C=200.00000000000003, gamma=0.41871642407674825, kernel=sigmoid, score=-21242.032, total=   0.0s
[CV] C=200.00000000000003, gamma=0.705163778379655, kernel=rbf .......
[CV]  C=200.00000000000003, gamma=0.705163778379655, kernel=rbf, score=0.236, total=   0.0s
[CV] C=200.00000000000003, gamma=0.705163778379655, kernel=rbf .......
[CV]  C=200.00000000000003, gamma=0.705163778379655, kernel=rbf, score=0.063, total=   0.0s
[CV] C=200.00000000000003, gamma=0.705163778379655, kernel=rbf .......
[CV]  C=200.00000000000003, gamma=0.705163778379655, kernel=rbf, score=0.064, total=   0.0s
[CV] C=200.00000000000003, gamma=0.705163778379655, kernel=rbf .......
[CV]  C=200.00000000000003, gamma=0.705163778379655, kernel=rbf, score=0.047, total=   0.0s
[CV] C=200.00000000000003, gamma=0.705163778379655, kernel=rbf .......
[CV]  C=200.00000000000003, gamma=0.705163778379655, kernel=rbf, score=-0.274, total=   0.0s
[CV] C=200.00000000000003, gamma=0.705163778379655, kernel=sigmoid ...
[CV]  C=20

[Parallel(n_jobs=1)]: Done 4000 out of 4000 | elapsed:  1.5min finished


In [11]:
print(f'Best params: {model.best_params_}')
test.head()

Best params: {'C': 8.054194294753, 'gamma': 0.24862797716933557, 'kernel': 'rbf'}


Survived  Pclass  SibSp  Parch     Fare    new_age
5          0       3      0      0   8.4583  25.963382
17         1       2      0      0  13.0000  31.287189
19         1       3      0      0   7.2250  22.100389
26         0       3      0      0   7.2250  26.366350
28         1       3      0      0   7.8792  23.955973

#### Predição Cabine

In [12]:
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.tree import DecisionTreeClassifier

In [13]:
titanic = titanic_orig.copy()
titanic.drop(['Name','Fare', 'Ticket'], axis=1, inplace = True)

genders = {'male': 0, 'female': 1}
titanic['Sex'] = titanic['Sex'].map(genders)

ports = {'S': 0, 'C': 1, 'Q': 2}
titanic['Embarked'] = titanic['Embarked'].map(ports)

test = titanic[titanic['Cabin'].isnull()]
titanic.dropna(inplace=True)

titanic['Cabin'] = pd.Categorical(titanic['Cabin'])
titanic['Cabin_code'] = titanic['Cabin'].cat.codes
titanic.drop(['Cabin'], axis=1, inplace = True)

bins = [0, 10, 20, 30, 40, 50, 60, np.inf]
names = [1, 2, 3, 4, 5, 6, 7]
titanic['Age'] = pd.cut(titanic['Age'], bins=bins, labels=names)
titanic.head()

Survived  Pclass  Sex Age  SibSp  Parch  Embarked  Cabin_code
1          1       1    1   4      1      0       1.0          72
3          1       1    1   4      1      0       0.0          48
6          0       1    0   6      0      0       0.0         117
10         1       3    1   1      1      1       0.0         131
11         1       1    1   6      0      0       0.0          43

In [14]:
X = titanic.drop(['Cabin_code'], 1)
y = titanic['Cabin_code']

parameters = {
    'criterion': ['gini','entropy'], 
    'max_depth': [4,6,8]
}

model = GridSearchCV(DecisionTreeClassifier(), param_grid=parameters, cv=2, verbose=10)
model.fit(X, y)

test.drop(['Cabin'], 1, inplace=True)
test.fillna(test.median(), inplace=True)

new_cabin = model.predict(test)
test['new_cabin'] = new_cabin

Fitting 2 folds for each of 6 candidates, totalling 12 fits
[CV] criterion=gini, max_depth=4 .....................................
[CV] ......... criterion=gini, max_depth=4, score=0.054, total=   0.0s
[CV] criterion=gini, max_depth=4 .....................................
[CV] ......... criterion=gini, max_depth=4, score=0.066, total=   0.0s
[CV] criterion=gini, max_depth=6 .....................................
[CV] ......... criterion=gini, max_depth=6, score=0.087, total=   0.0s
[CV] criterion=gini, max_depth=6 .....................................
[CV] ......... criterion=gini, max_depth=6, score=0.099, total=   0.0s
[CV] criterion=gini, max_depth=8 .....................................
[CV] ......... criterion=gini, max_depth=8, score=0.109, total=   0.0s
[CV] criterion=gini, max_depth=8 .....................................
[CV] ......... criterion=gini, max_depth=8, score=0.132, total=   0.0s
[CV] criterion=entropy, max_depth=4 ..................................
[CV] ...... crite

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   4 out of   4 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   6 out of   6 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   7 out of   7 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   9 out of   9 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done  12 out of  12 | elapsed:    0.1s finished


In [15]:
print(f'Best params: {model.best_params_}')
test.head()

Best params: {'criterion': 'gini', 'max_depth': 8}


Survived  Pclass  Sex   Age  SibSp  Parch  Embarked  new_cabin
0         0       3    0  22.0      1      0       0.0        126
2         1       3    1  26.0      0      0       0.0        126
4         0       3    0  35.0      0      0       0.0        126
5         0       3    0  26.0      0      0       2.0        126
7         0       3    0   2.0      3      1       0.0         55

### Dealing with attribute noise/outliers

#### Z-score

In [16]:
titanic = titanic_orig.copy()
titanic.drop(['Name','Ticket','Cabin', 'Sex', 'Embarked'], axis=1, inplace = True)
cols = list(titanic.columns)

for c in cols:
    col_zscore = c + '_zscore'
    titanic[col_zscore ] = (titanic[c] - titanic[c].mean()) / titanic[c].std(ddof=0)
    
titanic.head()

Survived  Pclass   Age  SibSp  Parch     Fare  Survived_zscore  \
0         0       3  22.0      1      0   7.2500        -0.789272   
1         1       1  38.0      1      0  71.2833         1.266990   
2         1       3  26.0      0      0   7.9250         1.266990   
3         1       1  35.0      1      0  53.1000         1.266990   
4         0       3  35.0      0      0   8.0500        -0.789272   

   Pclass_zscore  Age_zscore  SibSp_zscore  Parch_zscore  Fare_zscore  
0       0.827377   -0.530377      0.432793     -0.473674    -0.502445  
1      -1.566107    0.571831      0.432793     -0.473674     0.786845  
2       0.827377   -0.254825     -0.474545     -0.473674    -0.488854  
3      -1.566107    0.365167      0.432793     -0.473674     0.420730  
4       0.827377    0.365167     -0.474545     -0.473674    -0.486337

In [17]:
titanic.query('Fare_zscore >4').head()

Survived  Pclass   Age  SibSp  Parch      Fare  Survived_zscore  \
27          0       1  19.0      3      2  263.0000        -0.789272   
88          1       1  23.0      3      2  263.0000         1.266990   
118         0       1  24.0      0      1  247.5208        -0.789272   
258         1       1  35.0      0      0  512.3292         1.266990   
299         1       1  50.0      0      1  247.5208         1.266990   

     Pclass_zscore  Age_zscore  SibSp_zscore  Parch_zscore  Fare_zscore  
27       -1.566107   -0.737041      2.247470      2.008933     4.647001  
88       -1.566107   -0.461489      2.247470      2.008933     4.647001  
118      -1.566107   -0.392601     -0.474545      0.767630     4.335332  
258      -1.566107    0.365167     -0.474545     -0.473674     9.667167  
299      -1.566107    1.398487     -0.474545      0.767630     4.335332

### Finding outlier tuples

In [18]:
from sklearn.neighbors import LocalOutlierFactor

In [19]:
titanic = titanic_orig.copy()
titanic.drop(['Name','Ticket','Cabin', 'Sex', 'Embarked'], axis=1, inplace = True)
titanic.dropna(inplace=True)

clf = LocalOutlierFactor(n_neighbors=3)
titanic['is_outlier'] = clf.fit_predict(titanic)
titanic.head()

Survived  Pclass   Age  SibSp  Parch     Fare  is_outlier
0         0       3  22.0      1      0   7.2500          -1
1         1       1  38.0      1      0  71.2833           1
2         1       3  26.0      0      0   7.9250          -1
3         1       1  35.0      1      0  53.1000           1
4         0       3  35.0      0      0   8.0500           1

In [20]:
nonoutliers = titanic.query('is_outlier==-1')
nonoutliers.head()

Survived  Pclass   Age  SibSp  Parch     Fare  is_outlier
0          0       3  22.0      1      0   7.2500          -1
2          1       3  26.0      0      0   7.9250          -1
39         1       3  14.0      1      0  11.2417          -1
40         0       3  40.0      1      0   9.4750          -1
44         1       3  19.0      0      0   7.8792          -1

### Dealing with duplicates

In [21]:
!curl --remote-name \
     -H 'Accept: application/vnd.github.v3.raw' \
     --location https://media.geeksforgeeks.org/wp-content/uploads/employees.csv

employees_orig = pd.read_csv("employees.csv") 

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 59175  100 59175    0     0  52182      0  0:00:01  0:00:01 --:--:-- 52182


#### Drop duplicates

In [22]:
employees = employees_orig.copy()
employees.sort_values('First Name', inplace=True)

employees.drop_duplicates(subset ="First Name", keep = 'first', inplace = True) 
employees.head()

First Name  Gender Start Date Last Login Time  Salary  Bonus %  \
101      Aaron    Male  2/17/2012        10:20 AM   61602   11.849   
137       Adam    Male  5/21/2011         1:45 AM   95327   15.120   
300       Alan    Male  6/26/1988         3:54 AM  111786    3.592   
372     Albert    Male   2/1/1997         4:20 PM   67827   19.717   
988      Alice  Female  10/5/2004         9:34 AM   47638   11.209   

    Senior Management             Team  
101              True        Marketing  
137             False     Distribution  
300              True      Engineering  
372              True      Engineering  
988             False  Human Resources

#### Deduplicação

In [23]:
#!pip install pandas-dedupe

In [25]:
import pandas_dedupe

employees_dedup = pandas_dedupe.dedupe_dataframe(employees_orig, ['First Name'])
employees_dedup

importing data ...


First Name : harry

First Name : None

0/10 positive, 0/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished


starting active labeling...
y


First Name : None

First Name : diana

1/10 positive, 0/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)revious


y


...

First Name : gregory

First Name : russell

11/10 positive, 3/10 negative
Do these records refer to the same thing?
(y)es / (n)o / (u)nsure / (f)inished / (p)revious


f


Finished labeling


clustering...
# duplicate sets 171


First Name  Gender Start Date Last Login Time  Salary             Bonus %  \
0    douglas    male   8/6/1993        12:42 pm   97308               6.945   
1     thomas    male  3/31/1996         6:53 am   61933                4.17   
2      maria  female  4/23/1993        11:17 am  130590  11.857999999999999   
3      jerry    male   3/4/2005         1:00 pm  138705                9.34   
4      larry    male  1/24/1998         4:47 pm  101004               1.389   

  Senior Management             Team  cluster id  confidence  
0              true        marketing         0.0    0.899529  
1              true             None         1.0    0.899529  
2             false          finance         2.0    0.899529  
3              true          finance         3.0    0.899529  
4              true  client services         4.0    0.899529

### Correlation

In [26]:
titanic = titanic_orig.copy()
titanic.drop(['Name','Ticket','Cabin', 'Sex', 'Embarked'], axis=1, inplace = True)

titanic.dropna(inplace=True)
pearsoncorr = titanic.corr(method='pearson')
print(pearsoncorr)

          Survived    Pclass       Age     SibSp     Parch      Fare
Survived  1.000000 -0.359653 -0.077221 -0.017358  0.093317  0.268189
Pclass   -0.359653  1.000000 -0.369226  0.067247  0.025683 -0.554182
Age      -0.077221 -0.369226  1.000000 -0.308247 -0.189119  0.096067
SibSp    -0.017358  0.067247 -0.308247  1.000000  0.383820  0.138329
Parch     0.093317  0.025683 -0.189119  0.383820  1.000000  0.205119
Fare      0.268189 -0.554182  0.096067  0.138329  0.205119  1.000000


#### Dados categóricos

In [27]:
titanic = titanic_orig.copy()
contingency_table = pd.crosstab(titanic['Sex'], titanic['Pclass'], margins=True)
print(contingency_table.head())

f_obs = np.array([contingency_table.iloc[0][0:3].values,
                  contingency_table.iloc[1][0:3].values])
f_obs

Pclass    1    2    3  All
Sex                       
female   94   76  144  314
male    122  108  347  577
All     216  184  491  891


array([[ 94,  76, 144],
       [122, 108, 347]])

In [28]:
from scipy import stats

stats.chi2_contingency(f_obs)[0:3]

(16.971499095517114, 0.00020638864348233114, 2)